In [88]:
import psycopg2
import pandas as pd
import numpy as np
import mariadb
import json
import os
import shutil
import subprocess
from pathlib import Path
import pyodbc
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from scipy.spatial import distance
import pickle
import matplotlib.pyplot as plt
from sklearn.impute import SimpleImputer
import seaborn as sns

In [89]:
os.getcwd()

'C:\\Users\\tsuma.thomas\\Documents\\Cropnuts\\DSML158\\SoilAnalysis'

In [90]:
soil_df = pd.read_csv("output/soil_analysis_cleaned.csv")

C:\Users\tsuma.thomas\AppData\Local\Temp\ipykernel_19460\3696429364.py:1: DtypeWarning: Columns (8) have mixed types. Specify dtype option on import or set low_memory=False.
  soil_df = pd.read_csv("output/soil_analysis_cleaned.csv")


In [91]:
soil_df.analysis_name = [ str(i).strip() for i in soil_df.analysis_name ]

In [92]:
new_samples_df = soil_df.loc[soil_df['batch_date'] > '2024-05-21'] 
soil_df = soil_df.loc[soil_df['batch_date'] <= '2024-05-21'] 

In [93]:
soil_df.analysis_name.value_counts().to_csv("output/modelling_analysis_value_counts.csv")
new_samples_df.analysis_name.value_counts().to_csv("output/test_analysis_value_counts.csv")

In [94]:
soil_df['chemical_name'] = [ i.lower().replace(" ","_").replace(".","").replace("(","").replace(")","").replace("/","").strip() for i in soil_df['chemical_name'] ]

In [95]:
for analysis in np.unique(soil_df['analysis_name']):
    print(analysis)
    df_ = soil_df.loc[soil_df['analysis_name']==analysis]
    df_ = pd.pivot_table(data=df_, values="result", index="sample_code", columns="chemical_name")
    print(len(df_))

    os.makedirs(f"output/boxplots/{analysis}",exist_ok=True)
    for column in df_.columns:
        # print(column)
        os.makedirs(f"output/chemical_null_count",exist_ok=True)
        plt.boxplot(df_[column])
        plt.savefig(f"output/boxplots/{analysis}/{column}.png")
        plt.clf()
        outlier_threshold = df_[column].quantile(0.99)
        # df_ = df_.loc[df_[column] <= outlier_threshold]
    df_.describe().to_csv(f"output/chemical_null_count/{analysis}.csv")
    print(len(df_))
    if(len(df_) == 0):
        continue
    os.makedirs(f"output/analysis",exist_ok=True)
    df_.to_csv(f"output/analysis/{analysis.strip()}.csv")
    

% Gypsum
40
40
% Organic Matter (OM)
5264
5264
% Soil Nitrogen (N)
5228
5228
AFSIS Std Wet Chemistry Soil Analysis
13086
13086
ATA Ethiopia Soil Analysis
4687
4687
Advanced Biological Farming Soil Audit
253
253
Aluminium in soil
24
24
Ammonium Acetate Cu & Zn
48
48
Available Nitrogen
4858
4858
Available Nitrogen in Soil
1259
1259
Basic Hybrid Plus
48
48
Basic Soil Analysis
8365
8365
Basic Soil Analysis (BSA)
2101
2101
Basic Soil Analysis with Recommendations
24269
24269
Basic Soil Scan
1856
1856
Basis Soil Scan
40
40
Bio-available Nutrient Analysis
30
30
Boron Analysis - Hot water
48
48
Bray 1 in Soil
248
248
Calcium Carbonates (Soil)
416
416
Carbon Analysis
606
606
Chromium in Soil
19
19
Cobalt in Soil
1
1
Complete Hybrid Soil plus
50
50
Complete Soil + Bio-available Nutrients Analysis
58
58
Complete Soil +Hp Analysis
1126
1126
Complete Soil Analysis
21038
21038
Complete Soil Analysis (Calcareous)
52
52
Complete Soil Analysis (M3)
14072
14072
Complete Soil Analysis (data only)
8261
82

<Figure size 640x480 with 0 Axes>

In [97]:
for analysis_file in os.listdir("output/analysis"):
    os.makedirs("./output/analysis_nulls_handled",exist_ok=True)
    print(analysis_file)
    analysis_df = pd.read_csv(f"output/analysis/{analysis_file}",index_col=0)
    nulls_df = analysis_df.isna().sum()
    no_samples = len(analysis_df)
    for chem, null_count in zip(nulls_df.index, nulls_df.values):
        if (null_count/no_samples) > 0.5:
          analysis_df = analysis_df.drop(chem, axis=1)
    analysis_df.to_csv(f"./output/analysis_nulls_handled/{analysis_file}")    

% Gypsum.csv
             %_gypsum
sample_code          
CA079SA0001       3.0
CA079SA0002       2.0
CA079SA0003       2.0
CA079SA0004       2.0
CA079SA0005       2.0
CA079SA0006       3.0
CA079SA0007       3.0
CA079SA0008       4.0
CA079SA0009       3.0
CA079SA0010       2.0
CA079SA0011       2.0
CA079SA0012       5.0
CA079SA0013       3.0
CA079SA0014       3.0
CA079SA0015       2.0
CA079SA0016       3.0
CA079SA0017       3.0
CA079SA0018       5.0
CA079SA0019       5.0
CA079SA0020       2.0
CA079SA0021       4.0
CA079SA0022       1.0
CA079SA0023       2.0
CA079SA0024       2.0
CA079SA0025       3.0
CA079SA0026       2.0
CA079SA0027       3.0
CA079SA0028       4.0
CA079SA0029       3.0
CA079SA0030       2.0
CA079SA0031       4.0
CA079SA0032       6.0
CA079SA0033       4.0
CA079SA0034       5.0
CA079SA0035       6.0
CA079SA0036       4.0
CA079SA0037       4.0
CA079SA0038       4.0
CA079SA0039       4.0
CA079SA0040       2.0
% Organic Matter (OM).csv
                   aluminium  boron  

In [98]:
# for analysis_file in os.listdir("output/analysis"):
#     os.makedirs("./output/pairplots",exist_ok=True)
#     analysis_df = pd.read_csv(f"output/analysis/{analysis_file}",index_col=0)
#     print(analysis_file.replace('.csv',''))
#     sns.pairplot(analysis_df)
#     print('Saving')
#     plt.savefig(f"output/pairplots/{analysis_file.replace('.csv','')}.png")
#     print('Saved')
#     plt.clf()

In [99]:
for analysis_file in os.listdir("output/analysis_nulls_handled"):
    print(analysis_file)
    analysis_df = pd.read_csv(f"output/analysis_nulls_handled/{analysis_file}",index_col=0)
    if len(analysis_df.columns) == 0:
        continue
    imp_mean = SimpleImputer(missing_values=np.nan, strategy='mean')
    analysis_df = pd.DataFrame(imp_mean.fit_transform(analysis_df), columns=analysis_df.columns, index=analysis_df.index)
    pickle.dump(imp_mean, open(f"models/imputers/{analysis_file.replace('csv','pkl')}","wb"))
    if(len(analysis_df.columns) == 1):
        print(analysis_file)
        continue
    sc = StandardScaler()
    pca = PCA()
    analysis_scaled = sc.fit_transform(analysis_df)
    pca.fit(analysis_scaled)
    pca_explained_variance_df = pd.DataFrame(zip(analysis_df.columns,pca.explained_variance_ratio_))
    pca_explained_variance_df.to_csv(f"output/pca_explained_variance_ratio/{analysis_file}")

    n_components = len(pca_explained_variance_df.loc[pca_explained_variance_df[1]>0.1])
    if n_components < 2:
        n_components = 2
        pca_explained_variance_df = pca_explained_variance_df.loc[pca_explained_variance_df[1]>0]
    else:
        pca_explained_variance_df = pca_explained_variance_df.loc[pca_explained_variance_df[1]>0.1]
    
    pca_chems = pca_explained_variance_df[0]
    pca = PCA(n_components=n_components)
    analysis_scaled = sc.fit_transform(analysis_df)
    pca_reduced_df = pca.fit_transform(analysis_scaled)
    analysis_scaled = pd.DataFrame(analysis_scaled,index=analysis_df.index)
    pca_reduced_df = pd.DataFrame(pca_reduced_df,index=analysis_df.index, columns=pca_chems[0:n_components])
    analysis_scaled.to_csv(f"output/analysis_scaled/{analysis_file}")
    pca_reduced_df.to_csv(f"output/pca_df/{analysis_file}")
    pickle.dump(sc, open(f"models/scalers/{analysis_file.replace('csv','pkl')}","wb"))
    pickle.dump(pca, open(f"models/pca/{analysis_file.replace('csv','pkl')}","wb"))

% Gypsum.csv
% Gypsum.csv
% Organic Matter (OM).csv
% Soil Nitrogen (N).csv
Advanced Biological Farming Soil Audit.csv
AFSIS Std Wet Chemistry Soil Analysis.csv
Aluminium in soil.csv
Aluminium in soil.csv
Ammonium Acetate Cu & Zn.csv
Ammonium Acetate Cu & Zn.csv
ATA Ethiopia Soil Analysis.csv
Available Nitrogen in Soil.csv
Available Nitrogen in Soil.csv
Available Nitrogen.csv
Basic Hybrid Plus.csv
Basic Hybrid Plus.csv
Basic Soil Analysis (BSA).csv
Basic Soil Analysis with Recommendations.csv
Basic Soil Analysis.csv
Basic Soil Scan.csv
Basic Soil Scan.csv
Basis Soil Scan.csv
Basis Soil Scan.csv
Bio-available Nutrient Analysis.csv
Boron Analysis - Hot water.csv
Boron Analysis - Hot water.csv
Bray 1 in Soil.csv
Bray 1 in Soil.csv
Calcium Carbonates (Soil).csv
Calcium Carbonates (Soil).csv
Carbon Analysis.csv
Chromium in Soil.csv
Chromium in Soil.csv
Cobalt in Soil.csv
Cobalt in Soil.csv
Complete Hybrid Soil plus.csv
Complete Hybrid Soil plus.csv
Complete Soil + Bio-available Nutrients An

In [100]:
for analysis_file in os.listdir("output/pca_df"):
    print(analysis_file)
    os.makedirs(f"output/mahalanobis_distance",exist_ok=True)
    pca_reduced_df = pd.read_csv(f"output/pca_df/{analysis_file}",index_col=0)
    # if len(pca_reduced_df.columns) < 2:
        # continue
    mu = np.mean(pca_reduced_df, axis=0)
    sigma = np.cov(pca_reduced_df.T)
    os.makedirs(f"output/pca_df",exist_ok=True)
    pca_reduced_df['mahalanobis_distance'] = [distance.mahalanobis(pca_reduced_df.iloc[i], mu, np.linalg.inv(sigma)) for i in range(len(pca_reduced_df)) ]

    pca_reduced_df.to_csv(f"output/mahalanobis_distance/{analysis_file}")

% Organic Matter (OM).csv
% Soil Nitrogen (N).csv
Advanced Biological Farming Soil Audit.csv
AFSIS Std Wet Chemistry Soil Analysis.csv
ATA Ethiopia Soil Analysis.csv
Available Nitrogen.csv
Basic Soil Analysis (BSA).csv
Basic Soil Analysis with Recommendations.csv
Basic Soil Analysis.csv
Bio-available Nutrient Analysis.csv
Carbon Analysis.csv
Complete Soil + Bio-available Nutrients Analysis.csv
Complete Soil +Hp Analysis.csv
Complete Soil Analysis (Calcareous).csv
Complete Soil Analysis (data only).csv
Complete Soil Analysis (M3).csv
Complete Soil Analysis - Co & Si (IFDC).csv
Complete Soil Analysis with Recommendations.csv
Complete Soil Analysis.csv
Estimated Available Water Holding Capacity.csv
Exch. Aluminium.csv
Exchangable Aluminium.csv
Exchangeable Acidity (Hp) Analysis.csv
Exchangeable Acidity (Hp) in Soil.csv
Exchangeable Acidity Analysis.csv
Free Lime in Soil.csv
Heavy Metal Analysis (Soil).csv
Heavy Metals Analysis.csv
Heavy Metals in Soil (Aqua regia).csv
Modified Morgan.csv


In [101]:
mahalanobis_threshold_dict = {}
for analysis_file in os.listdir("output/mahalanobis_distance"):
    print(analysis_file)
    os.makedirs(f"output/mahalanobis_distance_upper_quantile",exist_ok=True)
    os.makedirs(f"output/mahalanobis_boxplots",exist_ok=True)
    analysis = analysis_file.replace(".csv","")
    mahalanobis_df = pd.read_csv(f"output/mahalanobis_distance/{analysis_file}",index_col=0)
    upper_quantile = (mahalanobis_df['mahalanobis_distance'].quantile(0.95))
    mahalanobis_threshold_dict[analysis_file.replace(".csv","").strip()] = upper_quantile
    mahalanobis_df.loc[mahalanobis_df['mahalanobis_distance'] >= upper_quantile].to_csv(f"output/mahalanobis_distance_upper_quantile/{analysis_file}")
    plt.boxplot(mahalanobis_df['mahalanobis_distance'])
    plt.savefig(f"output/mahalanobis_boxplots/{analysis}.png")
    plt.clf()
pickle.dump(mahalanobis_threshold_dict, open("mahalanobis_thresholds.dict","wb"))

% Organic Matter (OM).csv
% Soil Nitrogen (N).csv
Advanced Biological Farming Soil Audit.csv
AFSIS Std Wet Chemistry Soil Analysis.csv
ATA Ethiopia Soil Analysis.csv
Available Nitrogen.csv
Basic Soil Analysis (BSA).csv
Basic Soil Analysis with Recommendations.csv
Basic Soil Analysis.csv
Bio-available Nutrient Analysis.csv
Carbon Analysis.csv
Complete Soil + Bio-available Nutrients Analysis.csv
Complete Soil +Hp Analysis.csv
Complete Soil Analysis (Calcareous).csv
Complete Soil Analysis (data only).csv
Complete Soil Analysis (M3).csv
Complete Soil Analysis - Co & Si (IFDC).csv
Complete Soil Analysis with Recommendations.csv
Complete Soil Analysis.csv
Estimated Available Water Holding Capacity.csv
Exch. Aluminium.csv
Exchangable Aluminium.csv
Exchangeable Acidity (Hp) Analysis.csv
Exchangeable Acidity (Hp) in Soil.csv
Exchangeable Acidity Analysis.csv
Free Lime in Soil.csv
Heavy Metal Analysis (Soil).csv
Heavy Metals Analysis.csv
Heavy Metals in Soil (Aqua regia).csv
Modified Morgan.csv


<Figure size 640x480 with 0 Axes>

In [102]:
mahalanobis_threshold_dict

{'% Organic Matter (OM)': 2.4787498452162673,
 '% Soil Nitrogen (N)': 2.8604639465957726,
 'Advanced Biological Farming Soil Audit': 2.6277811147643377,
 'AFSIS Std Wet Chemistry Soil Analysis': 3.550887899802413,
 'ATA Ethiopia Soil Analysis': 2.407677942274546,
 'Available Nitrogen': 3.02263491528631,
 'Basic Soil Analysis (BSA)': 2.631981622753651,
 'Basic Soil Analysis with Recommendations': 2.6127442789597994,
 'Basic Soil Analysis': 2.6059185031458965,
 'Bio-available Nutrient Analysis': 2.6727884621670746,
 'Carbon Analysis': 2.9064009713000245,
 'Complete Soil + Bio-available Nutrients Analysis': 2.2812465755613838,
 'Complete Soil +Hp Analysis': 3.046286458594179,
 'Complete Soil Analysis (Calcareous)': 2.8073289689165652,
 'Complete Soil Analysis (data only)': 2.373410937682215,
 'Complete Soil Analysis (M3)': 3.557909535958923,
 'Complete Soil Analysis - Co & Si (IFDC)': 2.599494670364461,
 'Complete Soil Analysis with Recommendations': 2.148327689493776,
 'Complete Soil Ana

In [41]:
pd.DataFrame({'analysis_name':mahalanobis_threshold_dict.keys()}).to_csv("output/analyses_in_models.csv")

In [42]:
conn_lims = pyodbc.connect("Driver={SQL Server};"
                            "Server=192.168.5.18\CROPNUT;"
                            "Database=cropnuts;"
                            "uid=thomasTsuma;pwd=GR^KX$uRe9#JwLc6")

In [43]:
analysis_dict = pd.read_sql(f"""SELECT analysis_id, LTRIM(RTRIM(analysis_name)) as analysis_name FROM Analysis  ORDER BY analysis_name""",con=conn_lims).set_index("analysis_id").to_dict()['analysis_name']
pickle.dump(analysis_dict, open("analysis.dict","wb"))

C:\Users\tsuma.thomas\AppData\Local\Temp\ipykernel_19460\1909864603.py:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  analysis_dict = pd.read_sql(f"""SELECT analysis_id, LTRIM(RTRIM(analysis_name)) as analysis_name FROM Analysis  ORDER BY analysis_name""",con=conn_lims).set_index("analysis_id").to_dict()['analysis_name']


In [44]:
reverse_analysis_dict = pd.read_sql(f"""SELECT analysis_id, LTRIM(RTRIM(analysis_name)) as analysis_name FROM Analysis ORDER BY analysis_name""",con=conn_lims).set_index("analysis_name").to_dict()['analysis_id']
reverse_analysis_dict

C:\Users\tsuma.thomas\AppData\Local\Temp\ipykernel_19460\3771434913.py:1: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  reverse_analysis_dict = pd.read_sql(f"""SELECT analysis_id, LTRIM(RTRIM(analysis_name)) as analysis_name FROM Analysis ORDER BY analysis_name""",con=conn_lims).set_index("analysis_name").to_dict()['analysis_id']


{'% Gypsum': 540,
 '% Nitrogen (RSSP 2)': 647,
 '% Organic Matter': 258,
 '% Organic Matter (RSSP 2)': 646,
 '% Soil Nitrogen': 18,
 '%Assay': 27235,
 '%N (RSSP 2)': 652,
 '%OM (RSSP 2)': 651,
 '%P,%S Analysis(Super Calcium)': 383,
 '1:2 Soil Volume Extract': 294,
 '1:2 soil volume extract': 25,
 '1:2 Soil Volume Extract (Data Only)': 27339,
 '1:2 Vol Extract for BLGG': 317,
 '20:12:12 (N,P205,K20) Analysis': 840,
 'Absorbance at 254nm': 26936,
 'Acid Detergent Fibre': 27063,
 'Acid Insoluble Ash': 27417,
 'Acid Insoluble Matter': 27108,
 'Acid titration': 26647,
 'Acid Value': 26971,
 'Advanced Biological Farming Soil Audit': 26521,
 'Advanced Soil Health Analysis': 27181,
 'Aerobic Mesophilic Count': 26649,
 'Aflatoxin': 26794,
 'Aflatoxin AFB1': 26938,
 'Aflatoxin B1': 26939,
 'Aflatoxin in feed': 767,
 'Aflatoxin M1': 27469,
 'Aflatoxin Total': 766,
 'AfSIS Standard Leaf Analysis': 633,
 'AFSIS Std Wet Chemistry Soil Analysis': 589,
 'Aggregate Stability': 26727,
 'Agrifi Soil Micr

In [45]:
[reverse_analysis_dict[i] for i in soil_df['analysis_name'].unique() if i in reverse_analysis_dict.keys()]

[221,
 751,
 117,
 568,
 589,
 529,
 26597,
 525,
 4,
 27461,
 27383,
 524,
 26684,
 779,
 58,
 504,
 764,
 27278,
 808,
 183,
 523,
 697,
 811,
 522,
 609,
 526,
 518,
 26606,
 26991,
 528,
 220,
 26737,
 531,
 297,
 532,
 539,
 601,
 236,
 209,
 26570,
 704,
 26603,
 27189,
 26521,
 219,
 27209,
 26519,
 939,
 27211,
 27210,
 296,
 26722,
 26758,
 229,
 540,
 905,
 27283,
 548,
 26564,
 198,
 27186,
 26681,
 27458]

In [46]:
test = []
for sample in new_samples_df.sample_code.unique():
    res = {}
    tmp_ = new_samples_df.loc[new_samples_df.sample_code == sample]
    res['sample_code'] = sample
    res['analysis_id'] = [ reverse_analysis_dict[i] for i in tmp_.analysis_name.unique() if i in reverse_analysis_dict.keys() ]
    for index,row in tmp_.iterrows():
        if row['result'] >= 0 :
            res[row['chemical_name']] = {'result': row['result'], 'unit_name': str(row['unit_name'])}
        else:
            res[row['chemical_name']] = {'result': 0, 'unit_name': row['unit_name']}
    test.append(res)

In [47]:
str(test).replace("'",'"')

'[{"sample_code": "CB044SA0642", "analysis_id": [221], "organic_carbon": {"result": 1.53, "unit_name": "%"}, "c/n_ratio": {"result": 10.9, "unit_name": "nan"}, "ec_salts": {"result": 179.0, "unit_name": "uS/cm"}, "boron": {"result": 1.29, "unit_name": "ppm"}, "copper": {"result": 14.0, "unit_name": "ppm"}, "ph": {"result": 7.56, "unit_name": "nan"}, "total_nitrogen": {"result": 0.14, "unit_name": "%"}, "zinc": {"result": 19.6, "unit_name": "ppm"}, "calcium": {"result": 4490.0, "unit_name": "ppm"}, "magnesium": {"result": 726.0, "unit_name": "ppm"}, "potassium": {"result": 1230.0, "unit_name": "ppm"}, "sodium": {"result": 54.6, "unit_name": "ppm"}, "sulphur": {"result": 48.2, "unit_name": "ppm"}, "manganese": {"result": 253.0, "unit_name": "ppm"}, "iron": {"result": 85.4, "unit_name": "ppm"}}, {"sample_code": "CB044SA0639", "analysis_id": [221], "organic_carbon": {"result": 1.71, "unit_name": "%"}, "c/n_ratio": {"result": 12.2, "unit_name": "nan"}, "ec_salts": {"result": 226.0, "unit_na

In [103]:
req_body = test
_ = pd.DataFrame(req_body)
unit_decision = pd.read_csv("output/soil_unit_per_chemical_decision.csv")
unit_decision['chemical_name'] = [ i.lower().replace(" ","_").replace(".","").replace("(","").replace(")","").replace("/","").strip() for i in unit_decision['chemical_name']]
analysis_dict = pickle.load(open("analysis.dict","rb"))
mahalanobis_thresholds = pickle.load(open("mahalanobis_thresholds.dict","rb"))
result = {}
_df = _.explode('analysis_id', ignore_index=True)
for col in _df.columns:
    _df = _df.rename(columns={col: col.lower().replace(" ","_").replace(".","").replace("(","").replace(")","").replace("/","").strip()})
for index,row in _df.iterrows():
    sample_code = str(row['sample_code']).strip()
    result[sample_code] = []
    import math
    analysis_id = row['analysis_id']
    if math.isnan(analysis_id):
        result[sample_code].append({"sample_code": sample_code,"status":"warning", "message": f"Analysis not in specified", "details": f"Analysis id not provided" })   
        continue
    row['analysis_name'] = analysis_dict[analysis_id]
    analysis = row['analysis_name']
    
    print(analysis)
    if sample_code not in result.keys():
        result[sample_code] = []
    if analysis not in mahalanobis_thresholds.keys():
        result[sample_code].append({"sample_code": sample_code,"status":"warning", "message": f"Analysis not in models", "details": f"Analysis: {analysis} is not in the list of defined models" })   
        continue 
    row = row.dropna()
    scaler = pickle.load(open(f"models/scalers/{analysis}.pkl","rb"))
    pca = pickle.load(open(f"models/pca/{analysis}.pkl","rb"))
    imputer = pickle.load(open(f"models/imputers/{analysis}.pkl","rb"))
    pca_df = pd.read_csv(f"output/pca_df/{analysis}.csv",index_col=0)
    analysis_df = pd.read_csv(f"output/analysis_nulls_handled/{analysis}.csv",index_col=0)

    try :
        tmp_df = pd.DataFrame(row).T
        tmp_df = tmp_df[analysis_df.columns]
        
    except Exception as e:
        result[sample_code].append({"sample_code": sample_code,"status":"warning", "message": f"Missing parameters for analysis: {analysis}", "details": f"Expected parameters are {','.join([ i for i in analysis_df.columns if i not in tmp_df.columns])} for analysis: {analysis}"})
        continue
    if len([ i for i in analysis_df.columns if i not in tmp_df.columns]) > 0:
        result[sample_code].append({"sample_code": sample_code,"status":"warning", "message": f"Missing parameters for analysis: {analysis}", "details": f"Expected parameters are {','.join([ i for i in analysis_df.columns if i not in tmp_df.columns])} for analysis: {analysis}."})
        continue
    failed_units_comparison = {} 
    
    for col in pca_df.columns:
        expected_units = unit_decision.loc[(unit_decision['crop'] == analysis) & (unit_decision['chemical_name'] == col)]
        import math
        if len(expected_units) == 0 and math.isnan(row[col]['unit_name']) != True:
            failed_units_comparison[col] = {}
            failed_units_comparison[col]['expected_units'] = f"Units for {analysis} : {col} not defined"
        elif type(row[col]) != dict and math.isnan(row[col]):
            failed_units_comparison[col] = {}
            failed_units_comparison[col]['expected_units'] = expected_units['unit_name'].tolist()[0]
            failed_units_comparison[col]['units_provided'] = None
            print(col)
            print(failed_units_comparison)
        elif (row[col]['unit_name'] !=   expected_units['unit_name'].tolist()[0]) and type(row[col]['unit_name']) != str and math.isnan(row[col]['unit_name']) :
            failed_units_comparison[col] = {}
            failed_units_comparison[col]['expected_units'] = expected_units['unit_name'].tolist()[0]
            failed_units_comparison[col]['units_provided'] = row[col]['unit_name']
        else:
            continue     
    if len(failed_units_comparison.keys()) > 0:
        result[sample_code].append({"sample_code": sample_code,"status":"warning", "message": f"Wrong units provided", "details": f"Expected units are {str(failed_units_comparison)} for analysis: {analysis}" })
        continue
    for col in analysis_df.columns:
        if type(row[col]) == dict:
            row[col] = row[col]['result']
    
    # out_of_bounds_chems = [ ]
    # for col in tmp_df.columns:
    #     if col == "sample_code":
    #         continue
    #     if col == "ec_salts":
    #         if row[col] >= 105 or row[col] <= 95:
    #             out_of_bounds_chems.append("ec_salts out of bounds. Allowed bounds are 95 - 105")
    #     if col == "Charge Balance":
    #         if row[col] < -1:
    #             out_of_bounds_chems.append("Charge Balance out of bounds. Allowed lower boundary is -10. ")       
    #     elif col.lower() == "total suspended solids" and row['analysis_name'].lower() == "total suspended solids":
    #         if row[col] > 1:
    #             out_of_bounds_chems.append("total suspended solids out of bounds. If analysis is total suspended solids is <1 then total suspended solids check should be <1  . ")         
    # if len(out_of_bounds_chems) > 0:
    #     result[sample_code].append({"sample_code": sample_code,"status":"warning", "message": f"Out of bounds", "details": f"{'.'.join(out_of_bounds_chems)}" })
    #     continue    

    tmp_df = pd.DataFrame(row).T[analysis_df.columns]
    tmp_df = imputer.transform(tmp_df)
    df_scaled = scaler.transform(tmp_df)
    df_pca = pd.DataFrame(pca.transform(df_scaled))

    mu = np.mean(pca_df, axis=0)
    sigma = np.cov(pca_df.T)

    mahalanobis_distance = distance.mahalanobis(df_pca.iloc[0], mu, np.linalg.inv(sigma))


    expected_md = mahalanobis_thresholds[analysis]

    if mahalanobis_distance > expected_md:
        result[sample_code].append({"sample_code": sample_code,"status":"fail", "message": "Mahalanobis distance exceeds threshold", "details":f"Mahalanobis distance of {mahalanobis_distance} exceeds threshold of {expected_md} for analysis: {analysis}" })
    else:
        result[sample_code].append({"sample_code": sample_code,"status":"pass","message": "Mahalanobis distance within threshold", "details":f"Mahalanobis distance of {mahalanobis_distance} is within threshold of {expected_md} for analysis: {analysis}" })
        

Complete Soil Analysis with Recommendations
Complete Soil Analysis with Recommendations
Complete Soil Analysis with Recommendations
Complete Soil Analysis with Recommendations
Complete Soil Analysis with Recommendations


C:\Users\tsuma.thomas\AppData\Roaming\Python\Python39\site-packages\sklearn\base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(


Complete Soil Analysis with Recommendations
Complete Soil Analysis with Recommendations
Complete Soil Analysis with Recommendations


C:\Users\tsuma.thomas\AppData\Roaming\Python\Python39\site-packages\sklearn\base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(


Complete Soil Analysis with Recommendations
Complete Soil Analysis with Recommendations


...

C:\Users\tsuma.thomas\AppData\Roaming\Python\Python39\site-packages\sklearn\base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
C:\Users\tsuma.thomas\AppData\Roaming\Python\Python39\site-packages\sklearn\base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
C:\Users\tsuma.thomas\AppData\Roaming\Python\Python39\site-packages\sklearn\base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
C:\Users\tsuma.thomas\AppData\Roaming\Python\Python39\site-packages\sklearn\base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(


Complete Soil Analysis (data only)
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Soil pH in Water
Heavy Metals in Soil (Aqua regia)
Soil pH in Water
Heavy Metals in Soil (Aqua regia)
Soil pH in Water
Heavy Metals in Soil (Aqua regia)
Soil pH in Water
Heavy Metals in Soil (Aqua regia)
Soil pH in Water
Heavy Metals in Soil (Aqua regia)
Exchangeable Acidity (Hp) in Soil
Exchangeable Acidity (Hp) in Soil
Soil Bulk Density
Soil pH in K

C:\Users\tsuma.thomas\AppData\Roaming\Python\Python39\site-packages\sklearn\base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(


Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Density
Soil pH in KCL
Organic Matter (%) in Soil
Soil Bulk Den

TypeError: must be real number, not str

In [104]:
result

{'CB044SA0642': [{'sample_code': 'CB044SA0642',
   'status': 'warning',
   'message': 'Missing parameters for analysis: Complete Soil Analysis with Recommendations',
   'details': 'Expected parameters are phosphorus for analysis: Complete Soil Analysis with Recommendations'}],
 'CB044SA0639': [{'sample_code': 'CB044SA0639',
   'status': 'warning',
   'message': 'Missing parameters for analysis: Complete Soil Analysis with Recommendations',
   'details': 'Expected parameters are phosphorus for analysis: Complete Soil Analysis with Recommendations'}],
 'CB044SA0640': [{'sample_code': 'CB044SA0640',
   'status': 'warning',
   'message': 'Missing parameters for analysis: Complete Soil Analysis with Recommendations',
   'details': 'Expected parameters are phosphorus for analysis: Complete Soil Analysis with Recommendations'}],
 'CB044SA0641': [{'sample_code': 'CB044SA0641',
   'status': 'warning',
   'message': 'Missing parameters for analysis: Complete Soil Analysis with Recommendations',


In [59]:
test

[{'sample_code': 'CB044SA0642',
  'analysis_id': [221],
  'organic_carbon': {'result': 1.53, 'unit_name': '%'},
  'c/n_ratio': {'result': 10.9, 'unit_name': 'nan'},
  'ec_salts': {'result': 179.0, 'unit_name': 'uS/cm'},
  'boron': {'result': 1.29, 'unit_name': 'ppm'},
  'copper': {'result': 14.0, 'unit_name': 'ppm'},
  'ph': {'result': 7.56, 'unit_name': 'nan'},
  'total_nitrogen': {'result': 0.14, 'unit_name': '%'},
  'zinc': {'result': 19.6, 'unit_name': 'ppm'},
  'calcium': {'result': 4490.0, 'unit_name': 'ppm'},
  'magnesium': {'result': 726.0, 'unit_name': 'ppm'},
  'potassium': {'result': 1230.0, 'unit_name': 'ppm'},
  'sodium': {'result': 54.6, 'unit_name': 'ppm'},
  'sulphur': {'result': 48.2, 'unit_name': 'ppm'},
  'manganese': {'result': 253.0, 'unit_name': 'ppm'},
  'iron': {'result': 85.4, 'unit_name': 'ppm'}},
 {'sample_code': 'CB044SA0639',
  'analysis_id': [221],
  'organic_carbon': {'result': 1.71, 'unit_name': '%'},
  'c/n_ratio': {'result': 12.2, 'unit_name': 'nan'},


In [80]:
mahalanobis_thresholds

{'Complete Soil Analysis with Recommendations': 2.148327689493776,
 '% Organic Matter (OM)': 2.4787498452162673,
 '% Soil Nitrogen (N)': 2.8604639465957726,
 'Advanced Biological Farming Soil Audit': 2.6277811147643377,
 'AFSIS Std Wet Chemistry Soil Analysis': 3.550887899802413,
 'ATA Ethiopia Soil Analysis': 2.407677942274546,
 'Available Nitrogen in Soil': 1.1675633245872705,
 'Available Nitrogen': 3.02263491528631,
 'Basic Soil Analysis (BSA)': 2.631981622753651,
 'Basic Soil Analysis with Recommendations': 2.6127442789597994,
 'Basic Soil Analysis': 2.6059185031458965,
 'Bio-available Nutrient Analysis': 2.6727884621670746,
 'Calcium Carbonates (Soil)': 3.9381713169037664,
 'Carbon Analysis': 2.9064009713000245,
 'Complete Soil + Bio-available Nutrients Analysis': 2.2812465755613838,
 'Complete Soil +Hp Analysis': 3.046286458594179,
 'Complete Soil Analysis (Calcareous)': 2.8073289689165652,
 'Complete Soil Analysis (data only)': 2.373410937682215,
 'Complete Soil Analysis (M3)': 

In [105]:
final_df = pd.DataFrame()
for i in result.keys():
    out_df = (pd.DataFrame(result[i]))
    final_df = pd.concat([final_df, out_df])
final_df.to_csv("test_results.csv")